契約期間２&フル間取りでGOSSに交差検証法を試す。

In [13]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold

###訓練データの読み込み
house_age = pd.read_csv('house_age.csv')
area_size = pd.read_csv('area_size.csv')
room_arrange = pd.read_csv('room_arrange.csv')
contract_span = pd.read_csv('contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('reg_rent.csv')
floor_scores = pd.read_csv('floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('stations.csv')
minits = pd.read_csv('minits.csv')
addresses = pd.read_csv('addresses.csv')
room_arrange = pd.read_csv('room_arrange.csv')
buildings = pd.read_csv('buildings.csv')

rent = pd.read_csv('rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('test_house_age.csv')
test_area_size = pd.read_csv('test_area_size.csv')
test_room_arrange = pd.read_csv('test_room_arrange.csv')
test_contract_span = pd.read_csv('test_contract_span.csv')
test_contract_span2 = pd.read_csv('test_contract_span2.csv')
test_reg_rent = pd.read_csv('test_reg_rent.csv')
test_floor_scores = pd.read_csv('test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('test_capital_floor_scores2.csv')
test_stations = pd.read_csv('test_stations.csv')
test_minits = pd.read_csv('test_minits.csv')
test_addresses = pd.read_csv('test_addresses.csv')
test_room_arrange = pd.read_csv('test_room_arrange.csv')
test_buildings = pd.read_csv('test_buildings.csv')

In [7]:
X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, addresses, room_arrange[["部屋数","L","D","K",'S']]], axis=1)
y_train = rent

#X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.3, random_state=0)

X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_addresses, test_room_arrange[["部屋数","L","D","K",'S']]], axis=1)

category_lists = ['定期借家', '最寄り駅', '所在地', 'L', 'D', 'K','S']

cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    params = {
        'objective':'regression',
        'boosting_type':'goss',
        'metrics':'rmse',
        'learning_rate':0.05,
        'reg_lambda': 1.2667345328336822e-06,
        'max_bin': 405,
        'num_leaves': 118
    }

    model = lgb.train(
                        params,
                        lgb_train, 
                        valid_sets=[lgb_train, lgb_eval], 
                        verbose_eval=10, 
                        num_boost_round=1000, 
                        early_stopping_rounds=10,
                        categorical_feature = category_lists
                        )

y_pred = model.predict(X_test, num_iteration=model.best_iteration)

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001537 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2125
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 49712.4	valid_1's rmse: 52813.4
[20]	training's rmse: 35153.7	valid_1's rmse: 40945.6
[30]	training's rmse: 27250.7	valid_1's rmse: 34945.2
[40]	training's rmse: 22563.5	valid_1's rmse: 31659.1
[50]	training's rmse: 19563.3	valid_1's rmse: 29684.6
[60]	training's rmse: 17729.5	valid_1's rmse: 28401.5
[70]	training's rmse: 16460.1	valid_1's rmse: 27590
[80]	training's rmse: 15588.2	valid_1's rmse: 27036.5
[90]	training's rmse: 14881.7	valid_1's rmse: 26543.1
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001470 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2124
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118478.809819
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 50141.5	valid_1's rmse: 51820.2
[20]	training's rmse: 35997.3	valid_1's rmse: 38275.5
[30]	training's rmse: 28619.7	valid_1's rmse: 31518.7
[40]	training's rmse: 24234.4	valid_1's rmse: 27181
[50]	training's rmse: 21447.5	valid_1's rmse: 24580.6
[60]	training's rmse: 19701.8	valid_1's rmse: 23129.9
[70]	training's rmse: 18561.6	valid_1's rmse: 22265.3
[80]	training's rmse: 17603.6	valid_1's rmse: 21694.7
[90]	training's rmse: 16758.2	valid_1's rmse: 21464.5
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[10]	training's rmse: 50848.1	valid_1's rmse: 49993.6
[20]	training's rmse: 36719.2	valid_1's rmse: 36433.4
[30]	training's rmse: 29318.1	valid_1's rmse: 29109.1
[40]	training's rmse: 24793.6	valid_1's rmse: 25207.7
[50]	training's rmse: 21930	valid_1's rmse: 22737.2
[60]	training's rmse: 20186.2	valid_1's rmse: 21652.2
[70]	training's rmse: 19007.3	valid_1's rmse: 20884
[80]	training's rmse: 18104.3	valid_1's rmse: 20352.7
[90]	training's rmse: 17335.8	valid_1's rmse: 19947.5
[100]	training's rmse: 16714.8	valid_1's rmse: 19729.9
[110]	training's rmse: 16222.5	valid_1's rmse: 19543.1
[120]	training's rmse: 15750.2	valid_1's rmse: 19347.8
[130]	training's rmse: 15397.8	valid_1's rmse: 19247.6
[140]	training's rmse: 15017.9	valid_1's rmse: 19114.1
[150]	training's rmse: 14671.3	valid_1's rmse: 19019.6
[160]	training's rmse: 14404.8	valid_1's rmse: 18966.9
[170]	training's rmse: 14120.7	valid_1's rmse: 18880
[180]	training's rmse: 13840.4	valid_1's rmse: 18828
[190]	training's rmse: 1361

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[10]	training's rmse: 51209	valid_1's rmse: 48697.2
[20]	training's rmse: 36701.6	valid_1's rmse: 36058.3
[30]	training's rmse: 28948.1	valid_1's rmse: 29459.9
[40]	training's rmse: 24335	valid_1's rmse: 25894.1
[50]	training's rmse: 21538.3	valid_1's rmse: 23745.9
[60]	training's rmse: 19696.6	valid_1's rmse: 22383.1
[70]	training's rmse: 18485.9	valid_1's rmse: 21562
[80]	training's rmse: 17631.5	valid_1's rmse: 20975.3
[90]	training's rmse: 16920.5	valid_1's rmse: 20555.5
[100]	training's rmse: 16312.7	valid_1's rmse: 20259.7
[110]	training's rmse: 15841.9	valid_1's rmse: 20044.8
[120]	training's rmse: 15424.6	valid_1's rmse: 19826.5
[130]	training's rmse: 15049.7	valid_1's rmse: 19668.6
[140]	training's rmse: 14672.4	valid_1's rmse: 19487.4
[150]	training's rmse: 14311.9	valid_1's rmse: 19321.5
[160]	training's rmse: 14044.5	valid_1's rmse: 19241.4
[170]	training's rmse: 13701.3	valid_1's rmse: 19096.4
[180]	training's rmse: 13434.3	valid_1's rmse: 19037.5
[190]	training's rmse: 13

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[10]	training's rmse: 50180.5	valid_1's rmse: 53087.8
[20]	training's rmse: 36371.4	valid_1's rmse: 39220.7
[30]	training's rmse: 28682.7	valid_1's rmse: 31627.6
[40]	training's rmse: 24251.4	valid_1's rmse: 26942.5
[50]	training's rmse: 21511.8	valid_1's rmse: 24119.6
[60]	training's rmse: 19944.4	valid_1's rmse: 22533.4
[70]	training's rmse: 18816	valid_1's rmse: 21475.6
[80]	training's rmse: 17886.6	valid_1's rmse: 20754.8
[90]	training's rmse: 17246.2	valid_1's rmse: 20264.5
[100]	training's rmse: 16703.9	valid_1's rmse: 19850.1
[110]	training's rmse: 16178.7	valid_1's rmse: 19553.2
[120]	training's rmse: 15707.8	valid_1's rmse: 19251.7
[130]	training's rmse: 15318.2	valid_1's rmse: 18982.6
[140]	training's rmse: 15004.9	valid_1's rmse: 18778
[150]	training's rmse: 14670.1	valid_1's rmse: 18584.5
[160]	training's rmse: 14385.5	valid_1's rmse: 18354
[170]	training's rmse: 14111.8	valid_1's rmse: 18210.9
[180]	training's rmse: 13883.5	valid_1's rmse: 18094.8
[190]	training's rmse: 13

In [8]:
df = pd.read_csv('test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('GOSS_cv_result.csv',index=False)

GOSSをクロスバリデーションでチューニング

In [9]:
X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, addresses, room_arrange[["部屋数","L","D","K",'S']]], axis=1)
y_train = rent
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_addresses, test_room_arrange[["部屋数","L","D","K","S"]]], axis=1)
category_lists = ['定期借家', '最寄り駅', '所在地', 'L', 'D', 'K', 'S']

cv = KFold(n_splits=5, shuffle=True, random_state=0)
rmse_scores = []
X_train['KFold'] = -1
#foldはvalidの対象となる値で０から４
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_train.loc[valid_index,'KFold'] = fold_id
    y_train.loc[valid_index,'KFold'] = fold_id

def objective(trial):
    #foldはvalidの対象となる値で０から４
    for fold in range(5):
        X_tr = X_train[X_train['KFold']!=fold].drop('KFold',axis=1)
        X_val = X_train[X_train['KFold']==fold].drop('KFold',axis=1)
        y_tr = y_train[y_train['KFold']!=fold].drop('KFold',axis=1)
        y_val = y_train[y_train['KFold']==fold].drop('KFold',axis=1)

        lgb_train = lgb.Dataset(X_tr, y_tr)
        lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
        params = {
            'objective':'regression',
            'boosting_type':'goss',
            'metrics':'rmse',
            'learning_rate':0.05,
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0000001, 0.0001, log=True),
            'max_bin': trial.suggest_int('max_bin', 255, 600),
            'num_leaves': trial.suggest_int('num_leaves', 50, 128),
        }

        model = lgb.train(
                            params,
                            lgb_train, 
                            valid_sets=[lgb_train, lgb_eval], 
                            verbose_eval=10, 
                            num_boost_round=3000, 
                            early_stopping_rounds=10,
                            categorical_feature = category_lists
                            )

        y_pred_val = model.predict(X_val, num_iteration=model.best_iteration)
        rmse_score = mean_squared_error(y_val, y_pred_val, squared=False)
    loss = np.mean(rmse_score)
    return loss

In [10]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)
study.best_params

[I 2022-09-11 00:10:16,234] A new study created in memory with name: no-name-79777dec-1b56-428e-ad76-ba488dadc443
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001461 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2347
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 49657.6	valid_1's rmse: 52813.6
[20]	training's rmse: 35224.3	valid_1's rmse: 40947.7
[30]	training's rmse: 27025.8	valid_1's rmse: 34700.1
[40]	training's rmse: 22360.3	valid_1's rmse: 31303.8
[50]	training's rmse: 19380.3	valid_1's rmse: 29207.6
[60]	training's rmse: 17480.4	valid_1's rmse: 27917.8
[70]	training's rmse: 16241.2	valid_1's rmse: 27091.9
[80]	training's rmse: 15358.7	valid_1's rmse: 26479.9
[90]	training's rmse: 14709.4	valid_1's rmse: 26050.5
[100]	trai

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001283 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2347
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118478.809819
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 50762.6	valid_1's rmse: 52740.7
[20]	training's rmse: 36709	valid_1's rmse: 38947.9
[30]	training's rmse: 29215.7	valid_1's rmse: 31588.2
[40]	training's rmse: 24743.7	valid_1's rmse: 27266.5
[50]	training's rmse: 21977.1	valid_1's rmse: 24631.6
[60]	training's rmse: 20245.3	valid_1's rmse: 23048.1
[70]	training's rmse: 18847.9	valid_1's rmse: 22400
[80]	training's rmse: 17941.6	valid_1's rmse: 21793.5
[90]	training's rmse: 17208.8	valid_1's rmse: 21713.8
[100]	training

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

...

[10]	training's rmse: 51042.8	valid_1's rmse: 48830.2
[20]	training's rmse: 36452.6	valid_1's rmse: 36129.2
[30]	training's rmse: 28725.4	valid_1's rmse: 29386.3
[40]	training's rmse: 24033.8	valid_1's rmse: 25742.4
[50]	training's rmse: 21229.8	valid_1's rmse: 23596.2
[60]	training's rmse: 19595.5	valid_1's rmse: 22333.7
[70]	training's rmse: 18379.9	valid_1's rmse: 21553.1
[80]	training's rmse: 17521.5	valid_1's rmse: 21055
[90]	training's rmse: 16859.7	valid_1's rmse: 20713.7
[100]	training's rmse: 16362.1	valid_1's rmse: 20457.8
[110]	training's rmse: 15852.3	valid_1's rmse: 20325.5
[120]	training's rmse: 15439	valid_1's rmse: 20196.9
[130]	training's rmse: 15078.2	valid_1's rmse: 20039.2
[140]	training's rmse: 14710	valid_1's rmse: 19893
[150]	training's rmse: 14387.6	valid_1's rmse: 19722.3
[160]	training's rmse: 14115.8	valid_1's rmse: 19631.9
[170]	training's rmse: 13857.9	valid_1's rmse: 19546.1
[180]	training's rmse: 13634.2	valid_1's rmse: 19464.1
[190]	training's rmse: 1341

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001667 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2461
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118197.706188
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 50396.1	valid_1's rmse: 53168
[20]	training's rmse: 36591.4	valid_1's rmse: 39419.3
[30]	training's rmse: 29124.5	valid_1's rmse: 31835.1
[40]	training's rmse: 24662.6	valid_1's rmse: 27331.1
[50]	training's rmse: 21968.8	valid_1's rmse: 24431.2
[60]	training's rmse: 20222.2	valid_1's rmse: 22683.2
[70]	training's rmse: 19068.9	valid_1's rmse: 21583.6
[80]	training's rmse: 18199.5	valid_1's rmse: 20839.8
[90]	training's rmse: 17543.9	valid_1's rmse: 20316.1
[100]	traini

[I 2022-09-11 00:20:18,964] Trial 39 finished with value: 16248.958091395272 and parameters: {'reg_lambda': 5.543941231681784e-06, 'max_bin': 560, 'num_leaves': 104}. Best is trial 36 with value: 15783.79718784424.


{'reg_lambda': 4.669226029558975e-07, 'max_bin': 584, 'num_leaves': 85}

In [14]:
X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, addresses, room_arrange[["部屋数","L","D","K",'S']]], axis=1)
y_train = rent

#X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.3, random_state=0)

X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_addresses, test_room_arrange[["部屋数","L","D","K",'S']]], axis=1)

category_lists = ['定期借家', '最寄り駅', '所在地', 'L', 'D', 'K','S']

cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    params = {
        'objective':'regression',
        'boosting_type':'goss',
        'metrics':'rmse',
        'learning_rate':0.05,
        'reg_lambda': 4.669226029558975e-07,
        'max_bin': 584,
        'num_leaves': 85,
    }

    model = lgb.train(
                        params,
                        lgb_train, 
                        valid_sets=[lgb_train, lgb_eval], 
                        verbose_eval=10, 
                        num_boost_round=1000, 
                        early_stopping_rounds=10,
                        categorical_feature = category_lists
                        )

y_pred = model.predict(X_test, num_iteration=model.best_iteration)

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001786 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2511
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 49876.2	valid_1's rmse: 53024.8
[20]	training's rmse: 35307.7	valid_1's rmse: 41412.7
[30]	training's rmse: 27306.5	valid_1's rmse: 35496.8
[40]	training's rmse: 22571.2	valid_1's rmse: 32195.9
[50]	training's rmse: 19575.3	valid_1's rmse: 30099.9
[60]	training's rmse: 17719	valid_1's rmse: 28847.6
[70]	training's rmse: 16476.5	valid_1's rmse: 27952
[80]	training's rmse: 15633.6	valid_1's rmse: 27344.4
[90]	training's rmse: 14954.1	valid_1's rmse: 26862.1
[100]	training

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000881 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2511
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118478.809819
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 50637.1	valid_1's rmse: 52141.1
[20]	training's rmse: 36517.2	valid_1's rmse: 38397.3
[30]	training's rmse: 28867	valid_1's rmse: 30910.1
[40]	training's rmse: 24463.8	valid_1's rmse: 26862.3
[50]	training's rmse: 21656.2	valid_1's rmse: 24128.6
[60]	training's rmse: 19878.1	valid_1's rmse: 22743.5
[70]	training's rmse: 18736.3	valid_1's rmse: 21818.8
[80]	training's rmse: 17915.8	valid_1's rmse: 21248.6
[90]	training's rmse: 17233.1	valid_1's rmse: 20863.6
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[30]	training's rmse: 29116.1	valid_1's rmse: 28820.8
[40]	training's rmse: 24771.4	valid_1's rmse: 25108.8
[50]	training's rmse: 21985.8	valid_1's rmse: 22925.4
[60]	training's rmse: 20210.6	valid_1's rmse: 21649.9
[70]	training's rmse: 19039.7	valid_1's rmse: 20918.8
[80]	training's rmse: 18206.5	valid_1's rmse: 20526.1
[90]	training's rmse: 17509.4	valid_1's rmse: 20226.1
[100]	training's rmse: 16902.2	valid_1's rmse: 19983
[110]	training's rmse: 16376.2	valid_1's rmse: 19834.1
[120]	training's rmse: 15998.8	valid_1's rmse: 19712.5
[130]	training's rmse: 15631.8	valid_1's rmse: 19644.4
[140]	training's rmse: 15256.5	valid_1's rmse: 19482.1
[150]	training's rmse: 14908.2	valid_1's rmse: 19423.1
[160]	training's rmse: 14629.5	valid_1's rmse: 19383
[170]	training's rmse: 14344.6	valid_1's rmse: 19346.8
[180]	training's rmse: 14067.3	valid_1's rmse: 19302.5
[190]	training's rmse: 13830.8	valid_1's rmse: 19276.1
[200]	training's rmse: 13633.5	valid_1's rmse: 19206.9
[210]	training's rmse

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001248 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2513
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118323.873650
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 51147.6	valid_1's rmse: 48761.9
[20]	training's rmse: 36619.6	valid_1's rmse: 36148.2
[30]	training's rmse: 28793.7	valid_1's rmse: 29575.4
[40]	training's rmse: 24141.7	valid_1's rmse: 25824.3
[50]	training's rmse: 21337.8	valid_1's rmse: 23570.8
[60]	training's rmse: 19673.6	valid_1's rmse: 22233.3
[70]	training's rmse: 18402.2	valid_1's rmse: 21450.3
[80]	training's rmse: 17557.2	valid_1's rmse: 21054.6
[90]	training's rmse: 16881.7	valid_1's rmse: 20740.8
[100]	trai

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'K', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' ar

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000853 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2509
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118197.706188
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 50545.8	valid_1's rmse: 53286.4
[20]	training's rmse: 36855	valid_1's rmse: 39439.6
[30]	training's rmse: 29335.2	valid_1's rmse: 31791.1
[40]	training's rmse: 24928.2	valid_1's rmse: 27128.2
[50]	training's rmse: 22146.9	valid_1's rmse: 24183.5
[60]	training's rmse: 20325.5	valid_1's rmse: 22328.4
[70]	training's rmse: 19188.2	valid_1's rmse: 21192.1
[80]	training's rmse: 18283.5	valid_1's rmse: 20549.2
[90]	training's rmse: 17638	valid_1's rmse: 20094.8
[100]	training

In [15]:
df = pd.read_csv('test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('GOSS_cv_result.csv',index=False)

GOSSに「地価」情報を入れてみる

In [1]:
import pandas as pd


df_adachi = pd.read_csv('../data/handmade_data/block_aveprice_adachi2019.csv')
df_arakawa = pd.read_csv('../data/handmade_data/block_aveprice_arakawa2019.csv')
df_bunkyo = pd.read_csv('../data/handmade_data/block_aveprice_bunkyo2019.csv')
df_chiyoda = pd.read_csv('../data/handmade_data/block_aveprice_chiyoda2019.csv')
df_chuo = pd.read_csv('../data/handmade_data/block_aveprice_chuo2019.csv')
df_edogawa = pd.read_csv('../data/handmade_data/block_aveprice_edogawa2019.csv')
df_itabashi = pd.read_csv('../data/handmade_data/block_aveprice_itabashi2019.csv')
df_katsushika = pd.read_csv('../data/handmade_data/block_aveprice_katsushika2019.csv')
df_kita = pd.read_csv('../data/handmade_data/block_aveprice_kita2019.csv')
df_koto = pd.read_csv('../data/handmade_data/block_aveprice_koto2019.csv')
df_meguro = pd.read_csv('../data/handmade_data/block_aveprice_meguro2019.csv')
df_minato = pd.read_csv('../data/handmade_data/block_aveprice_minato2019.csv')
df_nakano = pd.read_csv('../data/handmade_data/block_aveprice_nakano2019.csv')
df_nerima = pd.read_csv('../data/handmade_data/block_aveprice_nerima2019.csv')
df_ota = pd.read_csv('../data/handmade_data/block_aveprice_ota2019.csv')
df_setagaya = pd.read_csv('../data/handmade_data/block_aveprice_setagaya2019.csv')
df_shibuya = pd.read_csv('../data/handmade_data/block_aveprice_shibuya2019.csv')
df_shinagawa = pd.read_csv('../data/handmade_data/block_aveprice_shinagawa2019.csv')
df_shinjuku = pd.read_csv('../data/handmade_data/block_aveprice_shinjuku2019.csv')
df_suginami = pd.read_csv('../data/handmade_data/block_aveprice_suginami2019.csv')
df_sumida = pd.read_csv('../data/handmade_data/block_aveprice_sumida2019.csv')
df_taito = pd.read_csv('../data/handmade_data/block_aveprice_taito2019.csv')
df_toshima = pd.read_csv('../data/handmade_data/block_aveprice_toshima2019.csv')

df_23wards = pd.concat([
    df_adachi,
    df_arakawa,
    df_bunkyo,
    df_chiyoda,
    df_chuo,
    df_edogawa,
    df_itabashi,
    df_katsushika,
    df_kita,
    df_koto,
    df_meguro,
    df_minato,
    df_nakano,
    df_nerima,
    df_ota,
    df_setagaya,
    df_shibuya,
    df_shinjuku,
    df_shinagawa,
    df_suginami,
    df_sumida,
    df_taito,
    df_toshima
],ignore_index=True)

addresses = pd.read_csv('../data/handmade_data/merge_address.csv')
addresses = addresses['所在地']
addresses = pd.DataFrame(addresses)

address_aveprice = pd.merge(addresses, df_23wards, left_on='所在地', right_on='0', how='left')
address_aveprice = address_aveprice[['所在地', '1']]
address_aveprice.columns = [['区町名', '平均地価']]

land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
land_aveprice.columns = ['平均地価']
test_land_aveprice.columns = ['平均地価']


import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]]], axis=1)
y_train = rent
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D","S"]]], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S']

Duplicate key in file PosixPath('/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/matplotlib/mpl-data/matplotlibrc'), line 258 ('font.family : IPAexGothic')
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


まずはチューニングをする

In [2]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
rmse_scores = []
X_train['KFold'] = -1
#foldはvalidの対象となる値で０から４
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_train.loc[valid_index,'KFold'] = fold_id
    y_train.loc[valid_index,'KFold'] = fold_id

def objective(trial):
    #foldはvalidの対象となる値で０から４
    for fold in range(5):
        X_tr = X_train[X_train['KFold']!=fold].drop('KFold',axis=1)
        X_val = X_train[X_train['KFold']==fold].drop('KFold',axis=1)
        y_tr = y_train[y_train['KFold']!=fold].drop('KFold',axis=1)
        y_val = y_train[y_train['KFold']==fold].drop('KFold',axis=1)

        lgb_train = lgb.Dataset(X_tr, y_tr)
        lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
        params = {
            'objective':'regression',
            'boosting_type':'goss',
            'metrics':'rmse',
            'learning_rate':0.05,
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0000001, 0.0001, log=True),
            'max_bin': trial.suggest_int('max_bin', 255, 600),
            'num_leaves': trial.suggest_int('num_leaves', 50, 128),
        }

        model = lgb.train(
                            params,
                            lgb_train, 
                            valid_sets=[lgb_train, lgb_eval], 
                            verbose_eval=10, 
                            num_boost_round=3000, 
                            early_stopping_rounds=10,
                            categorical_feature = category_lists
                            )

        y_pred_val = model.predict(X_val, num_iteration=model.best_iteration)
        rmse_score = mean_squared_error(y_val, y_pred_val, squared=False)
    loss = np.mean(rmse_score)
    return loss

In [3]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)

[I 2022-09-13 23:20:16,171] A new study created in memory with name: no-name-a5bd70b0-8a0e-4d94-b8f5-9ce0a9a059c4
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of L

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001008 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2822
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48789.7	valid_1's rmse: 52056.2
[20]	training's rmse: 34455.9	valid_1's rmse: 40332.3
[30]	training's rmse: 26138.7	valid_1's rmse: 33999.4
[40]	training's rmse: 21448.7	valid_1's rmse: 30693.8
[50]	training's rmse: 18709.6	valid_1's rmse: 28853.5
[60]	training's rmse: 16953.6	valid_1's rmse: 27694.3
[70]	training's rmse: 15795.8	valid_1's rmse: 26931.1
[80]	training's rmse: 15002.4	valid_1's rmse: 26345.4
[90]	training's rmse: 14379.2	valid_1's rmse: 25932.8
[100]	trai

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000878 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2821
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118478.809819
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 49459.2	valid_1's rmse: 49575.7
[20]	training's rmse: 35620.9	valid_1's rmse: 36058.2
[30]	training's rmse: 27888.9	valid_1's rmse: 28604
[40]	training's rmse: 23645.4	valid_1's rmse: 24817.6
[50]	training's rmse: 21072	valid_1's rmse: 22666.6
[60]	training's rmse: 19390.1	valid_1's rmse: 21442.4
[70]	training's rmse: 18368.1	valid_1's rmse: 20581.7
[80]	training's rmse: 17518.7	valid_1's rmse: 20128
[90]	training's rmse: 16676.6	valid_1's rmse: 19841.9
Early stopping, 

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

...

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[10]	training's rmse: 49401.6	valid_1's rmse: 48002.3
[20]	training's rmse: 35211.3	valid_1's rmse: 35440.3
[30]	training's rmse: 27110.1	valid_1's rmse: 28560.5
[40]	training's rmse: 22733.9	valid_1's rmse: 25195.8
[50]	training's rmse: 20129.9	valid_1's rmse: 23350.1
[60]	training's rmse: 18533.4	valid_1's rmse: 22269.1
[70]	training's rmse: 17382.4	valid_1's rmse: 21621.1
[80]	training's rmse: 16599.7	valid_1's rmse: 21310
[90]	training's rmse: 15999.4	valid_1's rmse: 20984.1
[100]	training's rmse: 15520.5	valid_1's rmse: 20774
[110]	training's rmse: 15097.9	valid_1's rmse: 20588.6
[120]	training's rmse: 14733.1	valid_1's rmse: 20449.8
[130]	training's rmse: 14380	valid_1's rmse: 20332.4
[140]	training's rmse: 14102.1	valid_1's rmse: 20206.8
[150]	training's rmse: 13831.3	valid_1's rmse: 20100.6
[160]	training's rmse: 13561	valid_1's rmse: 19975.1
[170]	training's rmse: 13336.2	valid_1's rmse: 19913.9
[180]	training's rmse: 13136.6	valid_1's rmse: 19874.3
[190]	training's rmse: 1291

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001270 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2979
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118197.706188
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48919	valid_1's rmse: 50885.2
[20]	training's rmse: 35260.1	valid_1's rmse: 36938.3
[30]	training's rmse: 27661.1	valid_1's rmse: 28941.7
[40]	training's rmse: 23435.1	valid_1's rmse: 24508.4
[50]	training's rmse: 20825.9	valid_1's rmse: 21689.4
[60]	training's rmse: 19233.7	valid_1's rmse: 20130.7
[70]	training's rmse: 18132.3	valid_1's rmse: 19069.2
[80]	training's rmse: 17269.1	valid_1's rmse: 18403
[90]	training's rmse: 16682.9	valid_1's rmse: 17942.6
[100]	training

[I 2022-09-13 23:28:58,138] Trial 39 finished with value: 14511.240704949429 and parameters: {'reg_lambda': 5.543941231681784e-06, 'max_bin': 560, 'num_leaves': 104}. Best is trial 4 with value: 13757.361123524024.


In [4]:
study.best_params

{'reg_lambda': 5.059803874660429e-06, 'max_bin': 575, 'num_leaves': 55}

チューニングで得た結果を使用する

In [8]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    params = {
        'objective':'regression',
        'boosting_type':'goss',
        'metrics':'rmse',
        'learning_rate':0.05,
        'reg_lambda': 5.059803874660429e-06,
        'max_bin': 575,
        'num_leaves': 55,
    }

    model = lgb.train(
                        params,
                        lgb_train, 
                        valid_sets=[lgb_train, lgb_eval], 
                        verbose_eval=10, 
                        num_boost_round=1000, 
                        early_stopping_rounds=10,
                        categorical_feature = category_lists
                        )

y_pred = model.predict(X_test, num_iteration=model.best_iteration)

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001595 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3018
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 49296.3	valid_1's rmse: 52602
[20]	training's rmse: 35136.4	valid_1's rmse: 40960.9
[30]	training's rmse: 26944.4	valid_1's rmse: 34637.1
[40]	training's rmse: 22233.2	valid_1's rmse: 31214.4
[50]	training's rmse: 19498.7	valid_1's rmse: 29189.6
[60]	training's rmse: 17810.3	valid_1's rmse: 27929
[70]	training's rmse: 16755	valid_1's rmse: 27136.1
[80]	training's rmse: 15973.6	valid_1's rmse: 26503.1
[90]	training's rmse: 15328.6	valid_1's rmse: 26030.1
[100]	training's

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000764 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3017
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118478.809819
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 49970.1	valid_1's rmse: 49929.4
[20]	training's rmse: 36218.1	valid_1's rmse: 36762.6
[30]	training's rmse: 28520.6	valid_1's rmse: 29226
[40]	training's rmse: 24282.9	valid_1's rmse: 25243.4
[50]	training's rmse: 21718	valid_1's rmse: 22748.2
[60]	training's rmse: 20113.6	valid_1's rmse: 21311.8
[70]	training's rmse: 19051.6	valid_1's rmse: 20442.3
[80]	training's rmse: 18224.2	valid_1's rmse: 19825.3
[90]	training's rmse: 17646.2	valid_1's rmse: 19493
[100]	training's

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[10]	training's rmse: 50019.8	valid_1's rmse: 49115.7
[20]	training's rmse: 36399.2	valid_1's rmse: 34824.9
[30]	training's rmse: 28566.3	valid_1's rmse: 26720.6
[40]	training's rmse: 24144.1	valid_1's rmse: 22787.1
[50]	training's rmse: 21613.2	valid_1's rmse: 20901.4
[60]	training's rmse: 19973.3	valid_1's rmse: 19878.1
[70]	training's rmse: 18866.3	valid_1's rmse: 19339.7
[80]	training's rmse: 18049.9	valid_1's rmse: 18995.1
[90]	training's rmse: 17436.1	valid_1's rmse: 18841.8
[100]	training's rmse: 16944.6	valid_1's rmse: 18683.6
[110]	training's rmse: 16551.5	valid_1's rmse: 18582
[120]	training's rmse: 16156.8	valid_1's rmse: 18474.6
[130]	training's rmse: 15748.8	valid_1's rmse: 18423.5
[140]	training's rmse: 15425.9	valid_1's rmse: 18399.6
[150]	training's rmse: 15092.8	valid_1's rmse: 18383.1
[160]	training's rmse: 14841.5	valid_1's rmse: 18338.7
[170]	training's rmse: 14585.4	valid_1's rmse: 18342.5
Early stopping, best iteration is:
[169]	training's rmse: 14610.6	valid_1's 

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[20]	training's rmse: 36111.7	valid_1's rmse: 36325.9
[30]	training's rmse: 28083.3	valid_1's rmse: 29553.3
[40]	training's rmse: 23672.6	valid_1's rmse: 25945
[50]	training's rmse: 20964.2	valid_1's rmse: 23956.3
[60]	training's rmse: 19381.8	valid_1's rmse: 22855.1
[70]	training's rmse: 18229.2	valid_1's rmse: 22056.1
[80]	training's rmse: 17443.2	valid_1's rmse: 21631.6
[90]	training's rmse: 16826.9	valid_1's rmse: 21427.6
[100]	training's rmse: 16300.2	valid_1's rmse: 21274.2
[110]	training's rmse: 15941.3	valid_1's rmse: 21102.9
[120]	training's rmse: 15592.2	valid_1's rmse: 20924.5
[130]	training's rmse: 15249.1	valid_1's rmse: 20801.8
[140]	training's rmse: 15000.3	valid_1's rmse: 20701.5
[150]	training's rmse: 14761.7	valid_1's rmse: 20666.9
[160]	training's rmse: 14535.3	valid_1's rmse: 20572.3
[170]	training's rmse: 14289.2	valid_1's rmse: 20406
[180]	training's rmse: 14074	valid_1's rmse: 20316.6
[190]	training's rmse: 13886.8	valid_1's rmse: 20224.1
[200]	training's rmse: 1

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[30]	training's rmse: 28518.1	valid_1's rmse: 29233.5
[40]	training's rmse: 24300.2	valid_1's rmse: 24518.1
[50]	training's rmse: 21780.6	valid_1's rmse: 21757.8
[60]	training's rmse: 20204.8	valid_1's rmse: 20196.8
[70]	training's rmse: 19098.4	valid_1's rmse: 19221.9
[80]	training's rmse: 18352.3	valid_1's rmse: 18526.6
[90]	training's rmse: 17711.4	valid_1's rmse: 18121.8
[100]	training's rmse: 17174.2	valid_1's rmse: 17762.8
[110]	training's rmse: 16807	valid_1's rmse: 17539.2
[120]	training's rmse: 16431.8	valid_1's rmse: 17399.3
[130]	training's rmse: 16113.3	valid_1's rmse: 17157.2
[140]	training's rmse: 15756.6	valid_1's rmse: 16888.2
[150]	training's rmse: 15494.1	valid_1's rmse: 16685
[160]	training's rmse: 15215.7	valid_1's rmse: 16520.7
[170]	training's rmse: 14967.7	valid_1's rmse: 16347.9
[180]	training's rmse: 14747.2	valid_1's rmse: 16195.3
[190]	training's rmse: 14553	valid_1's rmse: 16111.8
[200]	training's rmse: 14365.1	valid_1's rmse: 16046.2
[210]	training's rmse: 

In [9]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/GOSS_cv_result.csv',index=False)

「賃料」が50万以上のデータを除いてみる

In [2]:
X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]]], axis=1)
y_train = rent
all_train_DATA = pd.concat([y_train, X_train], axis=1)
all_train_DATA = all_train_DATA[all_train_DATA['賃料'] < 500000]

In [3]:
X_train = all_train_DATA.drop('賃料', axis=1)
y_train = all_train_DATA['賃料']

X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D","S"]]], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S']

In [4]:
X_train, X_valid, y_train, y_valid = train_test_split(X_train, y_train, test_size=0.2, random_state=0)
cv = KFold(n_splits=5, shuffle=True, random_state=0)

#これより交差検証のためにインデックスを振り直すので、最後にインデックスを元に戻すことに備えて元々のインデックスを退避させておく。
origin_index = X_train.index #origin_index = y_train.indexでも同じこと
X_train = X_train.reset_index()#交差検証のためにインデックス振り直し
X_train = X_train.drop('index', axis=1)##reset_index()をした結果、元のインデックスが"index"列として含まれてしまうので落としておく
y_train = y_train.reset_index()#交差検証のためにインデックス振り直し
y_train = y_train.drop('index',axis=1)##reset_index()をした結果、元のインデックスが"index"列として含まれてしまうので落としておく

cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    params = {
        'objective':'regression',
        'boosting_type':'goss',
        'metrics':'rmse',
        'learning_rate':0.05,
        'reg_lambda': 5.059803874660429e-06,
        'max_bin': 575,
        'num_leaves': 55,
    }

    model = lgb.train(
                        params,
                        lgb_train, 
                        valid_sets=[lgb_train, lgb_eval], 
                        verbose_eval=10, 
                        num_boost_round=1000, 
                        early_stopping_rounds=10,
                        categorical_feature = category_lists
                        )

y_pred = model.predict(X_test, num_iteration=model.best_iteration)

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[LightGBM] [Warning] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002556 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3002
[LightGBM] [Info] Number of data points in the train set: 20055, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 115551.405086
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 39125.8	valid_1's rmse: 39476.8
[20]	training's rmse: 27593.1	valid_1's rmse: 28674.7
[30]	training's rmse: 20798.5	valid_1's rmse: 22480.6
[40]	training's rmse: 17079.8	valid_1's rmse: 19222.2
[50]	training's rmse: 14920.6	valid_1's rmse: 17423.6
[60]	training's rmse: 13551	valid_1's rmse: 16269.2
[70]	training's rmse: 12660.4	valid_1's rmse: 15537.5
[80]	training's rmse: 12079.9	valid_1's rmse: 15083.3
[90]	training's rmse: 11639.2	valid_1's rmse: 14757
[100]	training's rmse: 11295.3	valid_1's rmse: 14523.3
[110]	training's rmse: 

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[30]	training's rmse: 20712	valid_1's rmse: 22109.3
[40]	training's rmse: 17003.9	valid_1's rmse: 18697.6
[50]	training's rmse: 14893.6	valid_1's rmse: 16849.2
[60]	training's rmse: 13549.7	valid_1's rmse: 15667.6
[70]	training's rmse: 12689.8	valid_1's rmse: 14990.2
[80]	training's rmse: 12090.8	valid_1's rmse: 14515.7
[90]	training's rmse: 11654.2	valid_1's rmse: 14238.8
[100]	training's rmse: 11304	valid_1's rmse: 14050.7
[110]	training's rmse: 11023.2	valid_1's rmse: 13903.6
[120]	training's rmse: 10784.9	valid_1's rmse: 13751.6
[130]	training's rmse: 10577.3	valid_1's rmse: 13659.3
[140]	training's rmse: 10372	valid_1's rmse: 13556.4
[150]	training's rmse: 10186.6	valid_1's rmse: 13470.9
[160]	training's rmse: 10014	valid_1's rmse: 13397.7
[170]	training's rmse: 9848.75	valid_1's rmse: 13330.3
[180]	training's rmse: 9705.45	valid_1's rmse: 13285.2
[190]	training's rmse: 9573.71	valid_1's rmse: 13240.8
[200]	training's rmse: 9432.07	valid_1's rmse: 13173.9
[210]	training's rmse: 92

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[20]	training's rmse: 27617.5	valid_1's rmse: 27915.9
[30]	training's rmse: 20910	valid_1's rmse: 21420.5
[40]	training's rmse: 17173.4	valid_1's rmse: 17907.2
[50]	training's rmse: 15096.3	valid_1's rmse: 16052.6
[60]	training's rmse: 13703.3	valid_1's rmse: 14873.7
[70]	training's rmse: 12790.2	valid_1's rmse: 14165.5
[80]	training's rmse: 12205.6	valid_1's rmse: 13741.2
[90]	training's rmse: 11779.5	valid_1's rmse: 13450.6
[100]	training's rmse: 11444.7	valid_1's rmse: 13233
[110]	training's rmse: 11151.3	valid_1's rmse: 13047.8
[120]	training's rmse: 10897.9	valid_1's rmse: 12907.3
[130]	training's rmse: 10684	valid_1's rmse: 12805
[140]	training's rmse: 10467.2	valid_1's rmse: 12709.4
[150]	training's rmse: 10286.5	valid_1's rmse: 12592.6
[160]	training's rmse: 10119.7	valid_1's rmse: 12496.7
[170]	training's rmse: 9958.78	valid_1's rmse: 12424
[180]	training's rmse: 9797.41	valid_1's rmse: 12350
[190]	training's rmse: 9656.21	valid_1's rmse: 12280.9
[200]	training's rmse: 9523.08

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[20]	training's rmse: 27636.1	valid_1's rmse: 27986.1
[30]	training's rmse: 20867.2	valid_1's rmse: 21460.3
[40]	training's rmse: 17162.6	valid_1's rmse: 18078.6
[50]	training's rmse: 15010.5	valid_1's rmse: 16203.6
[60]	training's rmse: 13613.1	valid_1's rmse: 15118.9
[70]	training's rmse: 12729.4	valid_1's rmse: 14520.8
[80]	training's rmse: 12135.4	valid_1's rmse: 14138.6
[90]	training's rmse: 11687.7	valid_1's rmse: 13861.9
[100]	training's rmse: 11355.8	valid_1's rmse: 13671.2
[110]	training's rmse: 11062.6	valid_1's rmse: 13529.4
[120]	training's rmse: 10797.9	valid_1's rmse: 13405.4
[130]	training's rmse: 10583.7	valid_1's rmse: 13307.3
[140]	training's rmse: 10383.3	valid_1's rmse: 13237.5
[150]	training's rmse: 10200	valid_1's rmse: 13164.1
[160]	training's rmse: 10037.6	valid_1's rmse: 13083.8
[170]	training's rmse: 9868.63	valid_1's rmse: 13027.5
[180]	training's rmse: 9714.21	valid_1's rmse: 12987.8
[190]	training's rmse: 9570.17	valid_1's rmse: 12946.3
[200]	training's rms

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_warning("'verbose_eval' argumen

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000952 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3012
[LightGBM] [Info] Number of data points in the train set: 20056, number of used features: 14
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 115769.414190
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 38962	valid_1's rmse: 39902.6
[20]	training's rmse: 27461.5	valid_1's rmse: 28842.2
[30]	training's rmse: 20718.9	valid_1's rmse: 22571.8
[40]	training's rmse: 16930.8	valid_1's rmse: 19163.8
[50]	training's rmse: 14844.8	valid_1's rmse: 17292.6
[60]	training's rmse: 13469.6	valid_1's rmse: 16130.3
[70]	training's rmse: 12607	valid_1's rmse: 15426.4
[80]	training's rmse: 12007.2	valid_1's rmse: 14947.4
[90]	training's rmse: 11571.1	valid_1's rmse: 14617.4
[100]	training

In [5]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/GOSS_cv_result.csv',index=False)

### 大きい「面積」にフラグを立てる

In [7]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D","S"]], over100m2, bt75and100m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D","S"]], test_over100m2, test_bt75and100m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','S', '100m^2以上', '75m^2以上100m^2未満']

チューニングを行う

In [2]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
rmse_scores = []
X_train['KFold'] = -1
#foldはvalidの対象となる値で０から４
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_train.loc[valid_index,'KFold'] = fold_id
    y_train.loc[valid_index,'KFold'] = fold_id

def objective(trial):
    #foldはvalidの対象となる値で０から４
    for fold in range(5):
        X_tr = X_train[X_train['KFold']!=fold].drop('KFold',axis=1)
        X_val = X_train[X_train['KFold']==fold].drop('KFold',axis=1)
        y_tr = y_train[y_train['KFold']!=fold].drop('KFold',axis=1)
        y_val = y_train[y_train['KFold']==fold].drop('KFold',axis=1)

        lgb_train = lgb.Dataset(X_tr, y_tr)
        lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
        params = {
            'objective':'regression',
            'boosting_type':'goss',
            'metrics':'rmse',
            'learning_rate':0.05,
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0000001, 0.0001, log=True),
            'max_bin': trial.suggest_int('max_bin', 255, 600),
            'num_leaves': trial.suggest_int('num_leaves', 50, 128),
        }

        model = lgb.train(
                            params,
                            lgb_train, 
                            valid_sets=[lgb_train, lgb_eval], 
                            verbose_eval=10, 
                            num_boost_round=3000, 
                            early_stopping_rounds=10,
                            categorical_feature = category_lists
                            )

        y_pred_val = model.predict(X_val, num_iteration=model.best_iteration)
        rmse_scores.append(mean_squared_error(y_val, y_pred_val, squared=False))
    loss = np.mean(rmse_scores)
    return loss

In [3]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)

[I 2022-09-15 14:44:46,522] A new study created in memory with name: no-name-fdc4fb9a-b4c9-4eda-a659-ed211f466fa9
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be r

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001670 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2827
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 16
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48789.7	valid_1's rmse: 50204
[20]	training's rmse: 34455.9	valid_1's rmse: 37892.9
[30]	training's rmse: 26010.6	valid_1's rmse: 30970.7
[40]	training's rmse: 21454.8	valid_1's rmse: 27503.4
[50]	training's rmse: 18618.9	valid_1's rmse: 25377.5
[60]	training's rmse: 16875.3	valid_1's rmse: 24074.9
[70]	training's rmse: 15835.3	valid_1's rmse: 23260.7
[80]	training's rmse: 15046.1	valid_1's rmse: 22629.1
[90]	training's rmse: 14430.2	valid_1's rmse: 22175.5
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000940 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2826
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 16
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118435.786702
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48983	valid_1's rmse: 49549.4
[20]	training's rmse: 34955.9	valid_1's rmse: 35957
[30]	training's rmse: 27065.8	valid_1's rmse: 28727.9
[40]	training's rmse: 22549.4	valid_1's rmse: 24724.9
[50]	training's rmse: 19935.3	valid_1's rmse: 22506.4
[60]	training's rmse: 18238.8	valid_1's rmse: 21245
[70]	training's rmse: 17191.6	valid_1's rmse: 20607.3
[80]	training's rmse: 16405.7	valid_1's rmse: 20090.6
[90]	training's rmse: 15794.2	valid_1's rmse: 19750.5
[100]	training's

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

...

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002131 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2986
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 16
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118280.850532
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48932.8	valid_1's rmse: 47994.3
[20]	training's rmse: 34587.6	valid_1's rmse: 35445.3
[30]	training's rmse: 26274.3	valid_1's rmse: 28898.7
[40]	training's rmse: 21680.8	valid_1's rmse: 25266.7
[50]	training's rmse: 19055.3	valid_1's rmse: 23483.3
[60]	training's rmse: 17387.3	valid_1's rmse: 22453
[70]	training's rmse: 16262.7	valid_1's rmse: 21681.6
[80]	training's rmse: 15437.8	valid_1's rmse: 21253.3
[90]	training's rmse: 14799.6	valid_1's rmse: 21044
[100]	training

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48450.2	valid_1's rmse: 50879.2
[20]	training's rmse: 34627.8	valid_1's rmse: 36937.9
[30]	training's rmse: 26717.2	valid_1's rmse: 28572.7
[40]	training's rmse: 22464.2	valid_1's rmse: 24137.8
[50]	training's rmse: 19927.8	valid_1's rmse: 21629.9
[60]	training's rmse: 18280.3	valid_1's rmse: 19983
[70]	training's rmse: 17049.8	valid_1's rmse: 18906.7
[80]	training's rmse: 16232.2	valid_1's rmse: 18218
[90]	training's rmse: 15604.1	valid_1's rmse: 17781.6
[100]	training's rmse: 15117.9	valid_1's rmse: 17408.5
[110]	training's rmse: 14655.7	valid_1's rmse: 17203.3
[120]	training's rmse: 14272.6	valid_1's rmse: 16978
[130]	training's rmse: 13902.9	valid_1's rmse: 16758.6
[140]	training's rmse: 13566.9	valid_1's rmse: 16568.3
[150]	training's rmse: 13273.3	valid_1's rmse: 16396.8
[160]	training's rmse: 13014.4	valid_1's rmse: 16246.4
[170]	training's rmse: 12776.9	valid_1's rmse: 16146.3
[180]	training's rm

[I 2022-09-15 14:54:44,283] Trial 39 finished with value: 17399.317544008903 and parameters: {'reg_lambda': 5.543941231681784e-06, 'max_bin': 560, 'num_leaves': 104}. Best is trial 3 with value: 17051.716458728406.


In [4]:
study.best_params

{'reg_lambda': 1.4135935551752292e-06, 'max_bin': 528, 'num_leaves': 91}

チューニング結果を使う

In [8]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    params = {
        'objective':'regression',
        'boosting_type':'goss',
        'metrics':'rmse',
        'learning_rate':0.05,
        'reg_lambda': 1.4135935551752292e-06,
        'max_bin': 528,
        'num_leaves': 91,
    }

    model = lgb.train(
                        params,
                        lgb_train, 
                        valid_sets=[lgb_train, lgb_eval], 
                        verbose_eval=10, 
                        num_boost_round=1000, 
                        early_stopping_rounds=10,
                        categorical_feature = category_lists
                        )

y_pred = model.predict(X_test, num_iteration=model.best_iteration)

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002498 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2901
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 16
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48780.2	valid_1's rmse: 50292
[20]	training's rmse: 34423.2	valid_1's rmse: 37937.7
[30]	training's rmse: 26091	valid_1's rmse: 31100.2
[40]	training's rmse: 21411.9	valid_1's rmse: 27484.2
[50]	training's rmse: 18635.7	valid_1's rmse: 25325
[60]	training's rmse: 16938.2	valid_1's rmse: 23974.6
[70]	training's rmse: 15846.1	valid_1's rmse: 23136.8
[80]	training's rmse: 15000.6	valid_1's rmse: 22411.4
[90]	training's rmse: 14408.9	valid_1's rmse: 21922.9
[100]	training's

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48942.7	valid_1's rmse: 49592.9
[20]	training's rmse: 34879.4	valid_1's rmse: 36624
[30]	training's rmse: 26726.2	valid_1's rmse: 29019.1
[40]	training's rmse: 22372.1	valid_1's rmse: 24996
[50]	training's rmse: 19653.8	valid_1's rmse: 22497.2
[60]	training's rmse: 18124.9	valid_1's rmse: 21246.9
[70]	training's rmse: 17002.4	valid_1's rmse: 20277.9
[80]	training's rmse: 16206.1	valid_1's rmse: 19641.3
[90]	training's rmse: 15575.6	valid_1's rmse: 19215.6
[100]	training's rmse: 15056	valid_1's rmse: 18928.2
[110]	training's rmse: 14625	valid_1's rmse: 18712.9
[120]	training's rmse: 14245.3	valid_1's rmse: 18551.1
[130]	training's rmse: 13889.6	valid_1's rmse: 18489.9
[140]	training's rmse: 13561.5	valid_1's rmse: 18441.8
[150]	training's rmse: 13264.3	valid_1's rmse: 18370.3
[160]	training's rmse: 12988.7	valid_1's rmse: 18270.2
[170]	training's rmse: 12670.3	valid_1's rmse: 18115.2
[180]	training's rmse

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

[30]	training's rmse: 27081.9	valid_1's rmse: 25874.9
[40]	training's rmse: 22756.6	valid_1's rmse: 22022.1
[50]	training's rmse: 20049.2	valid_1's rmse: 20113.1
[60]	training's rmse: 18300.1	valid_1's rmse: 19146.4
[70]	training's rmse: 17175.6	valid_1's rmse: 18592.2
[80]	training's rmse: 16280.4	valid_1's rmse: 18274.4
[90]	training's rmse: 15644.1	valid_1's rmse: 18063.8
[100]	training's rmse: 15137.3	valid_1's rmse: 17887.7
[110]	training's rmse: 14642.7	valid_1's rmse: 17806.4
[120]	training's rmse: 14266	valid_1's rmse: 17697.8
[130]	training's rmse: 13917.9	valid_1's rmse: 17620.1
[140]	training's rmse: 13538.9	valid_1's rmse: 17526.9
[150]	training's rmse: 13202.8	valid_1's rmse: 17480.8
[160]	training's rmse: 12873.9	valid_1's rmse: 17468.4
[170]	training's rmse: 12585.3	valid_1's rmse: 17494.4
Early stopping, best iteration is:
[163]	training's rmse: 12773.5	valid_1's rmse: 17451
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.00082

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

[10]	training's rmse: 49231	valid_1's rmse: 48194
[20]	training's rmse: 34974.3	valid_1's rmse: 35356
[30]	training's rmse: 26701.5	valid_1's rmse: 28172.8
[40]	training's rmse: 22203.7	valid_1's rmse: 24506
[50]	training's rmse: 19429.8	valid_1's rmse: 22507.2
[60]	training's rmse: 17757.2	valid_1's rmse: 21447.7
[70]	training's rmse: 16628.2	valid_1's rmse: 20794.1
[80]	training's rmse: 15870.6	valid_1's rmse: 20457.6
[90]	training's rmse: 15232.7	valid_1's rmse: 20058.2
[100]	training's rmse: 14733	valid_1's rmse: 19833.4
[110]	training's rmse: 14272.9	valid_1's rmse: 19610.2
[120]	training's rmse: 13891.7	valid_1's rmse: 19442.6
[130]	training's rmse: 13580.7	valid_1's rmse: 19353.2
[140]	training's rmse: 13280.3	valid_1's rmse: 19206.1
[150]	training's rmse: 12980.2	valid_1's rmse: 19132.8
[160]	training's rmse: 12714.7	valid_1's rmse: 19019.3
[170]	training's rmse: 12441.1	valid_1's rmse: 18929.1
[180]	training's rmse: 12211.3	valid_1's rmse: 18899.8
[190]	training's rmse: 12015.

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'L', 'S', '定期借家', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' argument instead.
  _log_

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001303 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2897
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 16
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118154.683071
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48740.4	valid_1's rmse: 51070.8
[20]	training's rmse: 34978.6	valid_1's rmse: 36978.2
[30]	training's rmse: 27114	valid_1's rmse: 28705.1
[40]	training's rmse: 22965.2	valid_1's rmse: 24440
[50]	training's rmse: 20282.1	valid_1's rmse: 21845.4
[60]	training's rmse: 18664.9	valid_1's rmse: 20294.3
[70]	training's rmse: 17539	valid_1's rmse: 19391.7
[80]	training's rmse: 16771.9	valid_1's rmse: 18809.2
[90]	training's rmse: 16158.5	valid_1's rmse: 18351.2
[100]	training's

In [9]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/GOSS_cv_result.csv',index=False)

特徴量を全て突っ込んでみる

In [8]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D",'K',"S"]], sepa_bath_toilets, washlets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'K','S']], test_sepa_bath_toilets, test_washlets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満']

In [6]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
rmse_scores = []
X_train['KFold'] = -1
#foldはvalidの対象となる値で０から４
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_train.loc[valid_index,'KFold'] = fold_id
    y_train.loc[valid_index,'KFold'] = fold_id

def objective(trial):
    #foldはvalidの対象となる値で０から４
    for fold in range(5):
        X_tr = X_train[X_train['KFold']!=fold].drop('KFold',axis=1)
        X_val = X_train[X_train['KFold']==fold].drop('KFold',axis=1)
        y_tr = y_train[y_train['KFold']!=fold].drop('KFold',axis=1)
        y_val = y_train[y_train['KFold']==fold].drop('KFold',axis=1)

        lgb_train = lgb.Dataset(X_tr, y_tr)
        lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
        params = {
            'objective':'regression',
            'boosting_type':'goss',
            'metrics':'rmse',
            'learning_rate':0.05,
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0000001, 0.0001, log=True),
            'max_bin': trial.suggest_int('max_bin', 255, 600),
            'num_leaves': trial.suggest_int('num_leaves', 50, 128),
        }

        model = lgb.train(
                            params,
                            lgb_train, 
                            valid_sets=[lgb_train, lgb_eval], 
                            verbose_eval=10, 
                            num_boost_round=3000, 
                            early_stopping_rounds=10,
                            categorical_feature = category_lists
                            )

        y_pred_val = model.predict(X_val, num_iteration=model.best_iteration)
        rmse_scores.append(mean_squared_error(y_val, y_pred_val, squared=False))
    loss = np.mean(rmse_scores)
    return loss

In [3]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)

[I 2022-09-15 23:11:03,759] A new study created in memory with name: no-name-f8c2816d-bed2-4b71-bc8c-d4eb8ec198dc
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is 

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001741 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2841
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 21
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48787.8	valid_1's rmse: 50198.5
[20]	training's rmse: 34378.4	valid_1's rmse: 37799.7
[30]	training's rmse: 25878.9	valid_1's rmse: 31003.4
[40]	training's rmse: 21314.2	valid_1's rmse: 27489.1
[50]	training's rmse: 18528.3	valid_1's rmse: 25372.6
[60]	training's rmse: 16776.4	valid_1's rmse: 24082.7
[70]	training's rmse: 15682.9	valid_1's rmse: 23245.9
[80]	training's rmse: 14854.2	valid_1's rmse: 22522.2
[90]	training's rmse: 14244.7	valid_1's rmse: 22030
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001082 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2840
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 21
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118435.786702
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48988.3	valid_1's rmse: 49544.9
[20]	training's rmse: 34966.4	valid_1's rmse: 36049.4
[30]	training's rmse: 26986	valid_1's rmse: 28711.1
[40]	training's rmse: 22659.3	valid_1's rmse: 24915.4
[50]	training's rmse: 19886.9	valid_1's rmse: 22565.3
[60]	training's rmse: 18152.3	valid_1's rmse: 21228.7
[70]	training's rmse: 17020.3	valid_1's rmse: 20372.2
[80]	training's rmse: 16170.6	valid_1's rmse: 19815.5
[90]	training's rmse: 15565.8	valid_1's rmse: 19472.2
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

...

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[10]	training's rmse: 48933.9	valid_1's rmse: 47996.4
[20]	training's rmse: 34574.2	valid_1's rmse: 35481.3
[30]	training's rmse: 26303	valid_1's rmse: 28593.6
[40]	training's rmse: 21797.5	valid_1's rmse: 25118.3
[50]	training's rmse: 19093.4	valid_1's rmse: 23214.3
[60]	training's rmse: 17452.7	valid_1's rmse: 22249.3
[70]	training's rmse: 16293.7	valid_1's rmse: 21579.1
[80]	training's rmse: 15450.3	valid_1's rmse: 21130
[90]	training's rmse: 14790.6	valid_1's rmse: 20725.1
[100]	training's rmse: 14312.4	valid_1's rmse: 20432.5
[110]	training's rmse: 13840.4	valid_1's rmse: 20282.7
[120]	training's rmse: 13449.6	valid_1's rmse: 20162.6
[130]	training's rmse: 13107	valid_1's rmse: 20062.3
[140]	training's rmse: 12812.1	valid_1's rmse: 19967.5
[150]	training's rmse: 12503.5	valid_1's rmse: 19871.5
[160]	training's rmse: 12264.9	valid_1's rmse: 19807.3
[170]	training's rmse: 12027.2	valid_1's rmse: 19704.9
[180]	training's rmse: 11775.3	valid_1's rmse: 19602.8
[190]	training's rmse: 11

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001628 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2999
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 21
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118154.683071
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48446.2	valid_1's rmse: 50891.5
[20]	training's rmse: 34581.2	valid_1's rmse: 36796.1
[30]	training's rmse: 26708.3	valid_1's rmse: 28532.4
[40]	training's rmse: 22281	valid_1's rmse: 23978.3
[50]	training's rmse: 19722.8	valid_1's rmse: 21430.7
[60]	training's rmse: 18067.9	valid_1's rmse: 19848.2
[70]	training's rmse: 16910.4	valid_1's rmse: 18769.5
[80]	training's rmse: 16078.5	valid_1's rmse: 18019.4
[90]	training's rmse: 15391.7	valid_1's rmse: 17518.1
[100]	traini

[I 2022-09-15 23:21:16,324] Trial 39 finished with value: 17205.77601636093 and parameters: {'reg_lambda': 5.543941231681784e-06, 'max_bin': 560, 'num_leaves': 104}. Best is trial 0 with value: 16919.45455218387.


In [4]:
study.best_params

{'reg_lambda': 4.430375245218262e-06, 'max_bin': 502, 'num_leaves': 97}

パラメータチューニングをする

In [9]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    params = {
        'objective':'regression',
        'boosting_type':'goss',
        'metrics':'rmse',
        'learning_rate':0.05,
        'reg_lambda': 4.430375245218262e-06,
        'max_bin': 502,
        'num_leaves': 97,
    }

    model = lgb.train(
                        params,
                        lgb_train, 
                        valid_sets=[lgb_train, lgb_eval], 
                        verbose_eval=10, 
                        num_boost_round=1000, 
                        early_stopping_rounds=10,
                        categorical_feature = category_lists
                        )

y_pred = model.predict(X_test, num_iteration=model.best_iteration)

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001816 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2841
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 21
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48787.8	valid_1's rmse: 50198.5
[20]	training's rmse: 34378.4	valid_1's rmse: 37799.7
[30]	training's rmse: 25878.9	valid_1's rmse: 31003.4
[40]	training's rmse: 21314.2	valid_1's rmse: 27489.1
[50]	training's rmse: 18528.3	valid_1's rmse: 25372.6
[60]	training's rmse: 16776.4	valid_1's rmse: 24082.7
[70]	training's rmse: 15682.9	valid_1's rmse: 23245.9
[80]	training's rmse: 14854.2	valid_1's rmse: 22522.2
[90]	training's rmse: 14244.7	valid_1's rmse: 22030
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[10]	training's rmse: 48988.3	valid_1's rmse: 49544.9
[20]	training's rmse: 34966.4	valid_1's rmse: 36049.4
[30]	training's rmse: 26986	valid_1's rmse: 28711.1
[40]	training's rmse: 22659.3	valid_1's rmse: 24915.4
[50]	training's rmse: 19886.9	valid_1's rmse: 22565.3
[60]	training's rmse: 18152.3	valid_1's rmse: 21228.7
[70]	training's rmse: 17020.3	valid_1's rmse: 20372.2
[80]	training's rmse: 16170.6	valid_1's rmse: 19815.5
[90]	training's rmse: 15565.8	valid_1's rmse: 19472.2
[100]	training's rmse: 15006.7	valid_1's rmse: 19202.2
[110]	training's rmse: 14541.3	valid_1's rmse: 19055.5
[120]	training's rmse: 14138	valid_1's rmse: 18950.1
[130]	training's rmse: 13791	valid_1's rmse: 18860.3
[140]	training's rmse: 13462.6	valid_1's rmse: 18832
[150]	training's rmse: 13175.5	valid_1's rmse: 18750.7
[160]	training's rmse: 12857.8	valid_1's rmse: 18705.1
[170]	training's rmse: 12574.8	valid_1's rmse: 18615.2
[180]	training's rmse: 12323.8	valid_1's rmse: 18573.6
[190]	training's rmse: 1204

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[10]	training's rmse: 49042.7	valid_1's rmse: 48424.6
[20]	training's rmse: 35382.2	valid_1's rmse: 33963.9
[30]	training's rmse: 27338.4	valid_1's rmse: 25610.6
[40]	training's rmse: 22771.7	valid_1's rmse: 21612.6
[50]	training's rmse: 20049.6	valid_1's rmse: 19654.5
[60]	training's rmse: 18265.5	valid_1's rmse: 18606.3
[70]	training's rmse: 17144.5	valid_1's rmse: 18177.8
[80]	training's rmse: 16294	valid_1's rmse: 17842.8
[90]	training's rmse: 15581.3	valid_1's rmse: 17607.5
[100]	training's rmse: 14992.2	valid_1's rmse: 17399.6
[110]	training's rmse: 14491.9	valid_1's rmse: 17279.9
[120]	training's rmse: 14099.5	valid_1's rmse: 17162.1
[130]	training's rmse: 13720.6	valid_1's rmse: 17157.7
[140]	training's rmse: 13402.5	valid_1's rmse: 17099.2
[150]	training's rmse: 13062.4	valid_1's rmse: 17083.4
[160]	training's rmse: 12743.8	valid_1's rmse: 17044
[170]	training's rmse: 12447.7	valid_1's rmse: 17028.7
[180]	training's rmse: 12200.6	valid_1's rmse: 17006
[190]	training's rmse: 11

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[10]	training's rmse: 49249	valid_1's rmse: 48181.2
[20]	training's rmse: 35071.7	valid_1's rmse: 35210.9
[30]	training's rmse: 26756.3	valid_1's rmse: 28172
[40]	training's rmse: 22149.3	valid_1's rmse: 24468.4
[50]	training's rmse: 19418.4	valid_1's rmse: 22612
[60]	training's rmse: 17784.4	valid_1's rmse: 21610.1
[70]	training's rmse: 16687.7	valid_1's rmse: 20865
[80]	training's rmse: 15841.5	valid_1's rmse: 20413.3
[90]	training's rmse: 15169.3	valid_1's rmse: 20122.7
[100]	training's rmse: 14679.4	valid_1's rmse: 19969
[110]	training's rmse: 14241.7	valid_1's rmse: 19827.8
[120]	training's rmse: 13864.3	valid_1's rmse: 19727.4
[130]	training's rmse: 13475	valid_1's rmse: 19557.6
[140]	training's rmse: 13130.8	valid_1's rmse: 19367.6
[150]	training's rmse: 12827.4	valid_1's rmse: 19201.8
[160]	training's rmse: 12568	valid_1's rmse: 19124.1
[170]	training's rmse: 12330.4	valid_1's rmse: 19058.3
[180]	training's rmse: 12095.6	valid_1's rmse: 18972.8
[190]	training's rmse: 11854.2	va

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback via 'callbacks' a

[20]	training's rmse: 34917.6	valid_1's rmse: 36975.2
[30]	training's rmse: 27114.1	valid_1's rmse: 28796.2
[40]	training's rmse: 22726.2	valid_1's rmse: 24275.4
[50]	training's rmse: 20108.8	valid_1's rmse: 21534.8
[60]	training's rmse: 18423.4	valid_1's rmse: 19949.6
[70]	training's rmse: 17254.5	valid_1's rmse: 19016.7
[80]	training's rmse: 16397.1	valid_1's rmse: 18370.6
[90]	training's rmse: 15773.2	valid_1's rmse: 18005.8
[100]	training's rmse: 15225.4	valid_1's rmse: 17737.1
[110]	training's rmse: 14714.5	valid_1's rmse: 17408.1
[120]	training's rmse: 14274.8	valid_1's rmse: 17067.9
[130]	training's rmse: 13845	valid_1's rmse: 16868.8
[140]	training's rmse: 13505.1	valid_1's rmse: 16692.5
[150]	training's rmse: 13170.6	valid_1's rmse: 16524.2
[160]	training's rmse: 12913.9	valid_1's rmse: 16426.3
[170]	training's rmse: 12687.5	valid_1's rmse: 16338.7
[180]	training's rmse: 12436.6	valid_1's rmse: 16210.9
[190]	training's rmse: 12228.5	valid_1's rmse: 16166.9
[200]	training's rms

In [10]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/GOSS_cv_result.csv',index=False)

### 「温水洗浄便座」と「方角」以外の全てを突っ込んでみる！

In [9]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
import scipy as sp
import lightgbm as lgb
import category_encoders as ce
# import mojimoji
import re
from cmath import nan
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import accuracy_score
import optuna
from sklearn.metrics import mean_squared_error
import japanize_matplotlib
from sklearn.model_selection import KFold
import xgboost
from catboost import CatBoostRegressor
from catboost import Pool

###訓練データの読み込み
house_age = pd.read_csv('../data/handmade_data/house_age.csv')
area_size = pd.read_csv('../data/handmade_data/area_size.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
contract_span = pd.read_csv('../data/handmade_data/contract_span.csv')#欠損値をゼロ埋めした契約期間
contract_span2 = pd.read_csv('../data/handmade_data/contract_span2.csv')#欠損値を欠損値のままにした契約期間
reg_rent = pd.read_csv('../data/handmade_data/reg_rent.csv')
floor_scores = pd.read_csv('../data/handmade_data/floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「所在階」
floor_scores2 = pd.read_csv('../data/handmade_data/floor_scores2.csv')#「所在階」と「全体の階数」が独立している「所在階」
Floor_scores = pd.read_csv('../data/handmade_data/capital_floor_scores.csv')#「所在階」と「全体の階数」が連動して欠損値になる場合のある「全体の階数」
Floor_scores2 = pd.read_csv('../data/handmade_data/capital_floor_scores2.csv')#「所在階」と「全体の階数」が独立している「全体の階数」
stations = pd.read_csv('../data/handmade_data/stations.csv')
minits = pd.read_csv('../data/handmade_data/minits.csv')
addresses = pd.read_csv('../data/handmade_data/addresses.csv')
room_arrange = pd.read_csv('../data/handmade_data/room_arrange.csv')
buildings = pd.read_csv('../data/handmade_data/buildings.csv')
land_aveprice = pd.read_csv('../data/handmade_data/land_aveprice.csv')
land_aveprice.columns = ['平均地価']
over100m2 = pd.read_csv('../data/handmade_data/over100m2.csv')
bt75and100m2 = pd.read_csv('../data/handmade_data/bt75and100m2.csv')
bt50and75m2 = pd.read_csv('../data/handmade_data/bt50and75m2.csv')
sepa_bath_toilets = pd.read_csv('../data/handmade_data/sepa_bath_toilets.csv')
sepa_bath_toilets.columns = ['バス・トイレ別']
washlets = pd.read_csv('../data/handmade_data/washlets.csv')

rent = pd.read_csv('../data/handmade_data/rent.csv')


##テストデータの読み込み
test_house_age = pd.read_csv('../data/test_data/test_house_age.csv')
test_area_size = pd.read_csv('../data/test_data/test_area_size.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_contract_span = pd.read_csv('../data/test_data/test_contract_span.csv')
test_contract_span2 = pd.read_csv('../data/test_data/test_contract_span2.csv')
test_contract_span2.columns = ['契約期間']
test_reg_rent = pd.read_csv('../data/test_data/test_reg_rent.csv')
test_floor_scores = pd.read_csv('../data/test_data/test_floor_scores.csv')
test_floor_scores2 = pd.read_csv('../data/test_data/test_floor_scores2.csv')
test_Floor_scores = pd.read_csv('../data/test_data/test_capital_floor_scores.csv')
test_Floor_scores2 = pd.read_csv('../data/test_data/test_capital_floor_scores2.csv')
test_stations = pd.read_csv('../data/test_data/test_stations.csv')
test_minits = pd.read_csv('../data/test_data/test_minits.csv')
test_addresses = pd.read_csv('../data/test_data/test_addresses.csv')
test_room_arrange = pd.read_csv('../data/test_data/test_room_arrange.csv')
test_buildings = pd.read_csv('../data/test_data/test_buildings.csv')
test_land_aveprice = pd.read_csv('../data/test_data/test_land_aveprice.csv')
test_land_aveprice.columns = ['平均地価']
test_over100m2 = pd.read_csv('../data/test_data/test_over100m2.csv')
test_bt75and100m2 = pd.read_csv('../data/test_data/test_bt75and100m2.csv')
test_bt50and75m2 = pd.read_csv('../data/test_data/test_bt50and75m2.csv')
test_sepa_bath_toilets = pd.read_csv('../data/test_data/test_sepa_bath_toilets.csv')
test_sepa_bath_toilets.columns = ['バス・トイレ別']
test_washlets = pd.read_csv('../data/test_data/test_washlets.csv')


X_train = pd.concat([house_age, area_size, contract_span2, reg_rent, floor_scores2, Floor_scores2, stations, minits, land_aveprice, addresses, room_arrange[["部屋数","L","D",'K',"S"]], sepa_bath_toilets, buildings, over100m2, bt75and100m2, bt50and75m2], axis=1)
y_train = pd.read_csv('../data/handmade_data/rent.csv')
y_train.loc[[5775], '賃料'] = y_train.loc[[5775], '賃料']/10
X_test = pd.concat([test_house_age, test_area_size, test_contract_span2, test_reg_rent, test_floor_scores2, test_Floor_scores2, test_stations, test_minits, test_land_aveprice, test_addresses, test_room_arrange[["部屋数","L","D",'K','S']],test_sepa_bath_toilets, test_buildings, test_over100m2, test_bt75and100m2, test_bt50and75m2], axis=1)
category_lists = ['定期借家','最寄り駅', '所在地', 'L', 'D','K', 'S', 'バス・トイレ別','建物構造','100m^2以上', '75m^2以上100m^2未満', '50m^2以上75m^2未満']

In [5]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
rmse_scores = []
X_train['KFold'] = -1
#foldはvalidの対象となる値で０から４
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_train.loc[valid_index,'KFold'] = fold_id
    y_train.loc[valid_index,'KFold'] = fold_id

def objective(trial):
    #foldはvalidの対象となる値で０から４
    for fold in range(5):
        X_tr = X_train[X_train['KFold']!=fold].drop('KFold',axis=1)
        X_val = X_train[X_train['KFold']==fold].drop('KFold',axis=1)
        y_tr = y_train[y_train['KFold']!=fold].drop('KFold',axis=1)
        y_val = y_train[y_train['KFold']==fold].drop('KFold',axis=1)

        lgb_train = lgb.Dataset(X_tr, y_tr)
        lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
        params = {
            'objective':'regression',
            'boosting_type':'goss',
            'metrics':'rmse',
            'learning_rate':0.05,
            'reg_lambda': trial.suggest_float('reg_lambda', 0.0000001, 0.0001, log=True),
            'max_bin': trial.suggest_int('max_bin', 255, 600),
            'num_leaves': trial.suggest_int('num_leaves', 50, 128),
        }

        model = lgb.train(
                            params,
                            lgb_train, 
                            valid_sets=[lgb_train, lgb_eval], 
                            verbose_eval=10, 
                            num_boost_round=3000, 
                            early_stopping_rounds=10,
                            categorical_feature = category_lists
                            )

        y_pred_val = model.predict(X_val, num_iteration=model.best_iteration)
        rmse_scores.append(mean_squared_error(y_val, y_pred_val, squared=False))
    loss = np.mean(rmse_scores)
    return loss

In [6]:
study = optuna.create_study(sampler=optuna.samplers.RandomSampler(seed=0))
study.optimize(objective, n_trials=40)

[I 2022-09-16 12:54:27,715] A new study created in memory with name: no-name-ec06e0be-2869-4b6c-b189-e30f465815ee
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002117 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2836
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 19
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48788	valid_1's rmse: 50195.8
[20]	training's rmse: 34383.9	valid_1's rmse: 37797.7
[30]	training's rmse: 25914.1	valid_1's rmse: 31042.1
[40]	training's rmse: 21232.9	valid_1's rmse: 27366
[50]	training's rmse: 18514.7	valid_1's rmse: 25313
[60]	training's rmse: 16808.1	valid_1's rmse: 24058.8
[70]	training's rmse: 15642.4	valid_1's rmse: 23135.1
[80]	training's rmse: 14840.4	valid_1's rmse: 22514.7
[90]	training's rmse: 14210.7	valid_1's rmse: 22054.6
[100]	training's

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001106 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2835
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 19
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118435.786702
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48981.1	valid_1's rmse: 49548
[20]	training's rmse: 34978.1	valid_1's rmse: 36020.2
[30]	training's rmse: 27032.4	valid_1's rmse: 28975.2
[40]	training's rmse: 22551.1	valid_1's rmse: 24747.6
[50]	training's rmse: 19967.4	valid_1's rmse: 22562.1
[60]	training's rmse: 18317.9	valid_1's rmse: 21311.9
[70]	training's rmse: 17230.1	valid_1's rmse: 20591.6
[80]	training's rmse: 16400.7	valid_1's rmse: 19974.1
[90]	training's rmse: 15710.1	valid_1's rmse: 19629.9
[100]	traini

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

...

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[20]	training's rmse: 34555.7	valid_1's rmse: 35575.3
[30]	training's rmse: 26251.8	valid_1's rmse: 28521.8
[40]	training's rmse: 21736.8	valid_1's rmse: 24927.7
[50]	training's rmse: 19050.4	valid_1's rmse: 23117.6
[60]	training's rmse: 17307.7	valid_1's rmse: 21872.9
[70]	training's rmse: 16247	valid_1's rmse: 21276.6
[80]	training's rmse: 15435	valid_1's rmse: 20811.7
[90]	training's rmse: 14858	valid_1's rmse: 20485
[100]	training's rmse: 14364.9	valid_1's rmse: 20336.7
[110]	training's rmse: 13920.3	valid_1's rmse: 20290.8
[120]	training's rmse: 13532.9	valid_1's rmse: 20214.5
[130]	training's rmse: 13204.8	valid_1's rmse: 20085.5
[140]	training's rmse: 12870.6	valid_1's rmse: 19997.3
[150]	training's rmse: 12578.6	valid_1's rmse: 19958.9
[160]	training's rmse: 12335.4	valid_1's rmse: 19860.6
[170]	training's rmse: 12076.5	valid_1's rmse: 19798.7
[180]	training's rmse: 11861.2	valid_1's rmse: 19673.4
[190]	training's rmse: 11641.5	valid_1's rmse: 19584.8
[200]	training's rmse: 114

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002111 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2994
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 19
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118154.683071
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48442.6	valid_1's rmse: 50903.8
[20]	training's rmse: 34632	valid_1's rmse: 36918.7
[30]	training's rmse: 26776.5	valid_1's rmse: 28708.4
[40]	training's rmse: 22380	valid_1's rmse: 24142.3
[50]	training's rmse: 19761.2	valid_1's rmse: 21526.1
[60]	training's rmse: 18081.8	valid_1's rmse: 19929.8
[70]	training's rmse: 16928.4	valid_1's rmse: 18895.6
[80]	training's rmse: 16151.5	valid_1's rmse: 18165.7
[90]	training's rmse: 15510.7	valid_1's rmse: 17681.4
[100]	training

[I 2022-09-16 13:04:59,020] Trial 39 finished with value: 17350.918714884127 and parameters: {'reg_lambda': 5.543941231681784e-06, 'max_bin': 560, 'num_leaves': 104}. Best is trial 3 with value: 17083.301620189093.


In [7]:
study.best_params

{'reg_lambda': 1.4135935551752292e-06, 'max_bin': 528, 'num_leaves': 91}

In [10]:
cv = KFold(n_splits=5, shuffle=True, random_state=0)
for fold_id, (train_index, valid_index) in enumerate(cv.split(X_train)):
    X_tr = X_train.loc[train_index,:]
    X_val = X_train.loc[valid_index, :]
    y_tr = y_train.loc[train_index]
    y_val = y_train.loc[valid_index]

    lgb_train = lgb.Dataset(X_tr, y_tr)
    lgb_eval = lgb.Dataset(X_val, y_val, reference=lgb_train)
    params = {
        'objective':'regression',
        'boosting_type':'goss',
        'metrics':'rmse',
        'learning_rate':0.05,
        'reg_lambda': 1.4135935551752292e-06,
        'max_bin': 528,
        'num_leaves': 91,
    }

    model = lgb.train(
                        params,
                        lgb_train, 
                        valid_sets=[lgb_train, lgb_eval], 
                        verbose_eval=10, 
                        num_boost_round=1000, 
                        early_stopping_rounds=10,
                        categorical_feature = category_lists
                        )

y_pred = model.predict(X_test, num_iteration=model.best_iteration)

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001680 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2910
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 19
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118516.069987
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48780.4	valid_1's rmse: 50292.9
[20]	training's rmse: 34411.6	valid_1's rmse: 37915.6
[30]	training's rmse: 25971.3	valid_1's rmse: 31065.6
[40]	training's rmse: 21267.7	valid_1's rmse: 27312.6
[50]	training's rmse: 18542.2	valid_1's rmse: 25186.9
[60]	training's rmse: 16846.8	valid_1's rmse: 23794.3
[70]	training's rmse: 15826.8	valid_1's rmse: 22958.1
[80]	training's rmse: 15002.5	valid_1's rmse: 22297.7
[90]	training's rmse: 14341.4	valid_1's rmse: 21739.5
[100]	trai

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001857 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2909
[LightGBM] [Info] Number of data points in the train set: 25176, number of used features: 19
[LightGBM] [Info] Using GOSS
[LightGBM] [Info] Start training from score 118435.786702
Training until validation scores don't improve for 10 rounds
[10]	training's rmse: 48950.3	valid_1's rmse: 49607.5
[20]	training's rmse: 34888	valid_1's rmse: 36677.4
[30]	training's rmse: 26730.3	valid_1's rmse: 29115.2
[40]	training's rmse: 22400.7	valid_1's rmse: 24945.9
[50]	training's rmse: 19745.6	valid_1's rmse: 22582.9
[60]	training's rmse: 18143.9	valid_1's rmse: 21135.2
[70]	training's rmse: 17001	valid_1's rmse: 20148.8
[80]	training's rmse: 16197.2	valid_1's rmse: 19497.8
[90]	training's rmse: 15593.9	valid_1's rmse: 19029.9
[100]	training

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[20]	training's rmse: 35249.8	valid_1's rmse: 34032.9
[30]	training's rmse: 27329.3	valid_1's rmse: 25905.6
[40]	training's rmse: 22717.3	valid_1's rmse: 21893.7
[50]	training's rmse: 19949.5	valid_1's rmse: 20071.1
[60]	training's rmse: 18283.3	valid_1's rmse: 19014.7
[70]	training's rmse: 17136.2	valid_1's rmse: 18469.4
[80]	training's rmse: 16358.5	valid_1's rmse: 18160.2
[90]	training's rmse: 15679.1	valid_1's rmse: 17989.9
[100]	training's rmse: 15102.4	valid_1's rmse: 17957.3
[110]	training's rmse: 14649.4	valid_1's rmse: 17825.3
[120]	training's rmse: 14258	valid_1's rmse: 17798.7
[130]	training's rmse: 13869.3	valid_1's rmse: 17727.7
[140]	training's rmse: 13508.8	valid_1's rmse: 17639.8
[150]	training's rmse: 13170.9	valid_1's rmse: 17631.1
Early stopping, best iteration is:
[148]	training's rmse: 13238.6	valid_1's rmse: 17615.9
[LightGBM] [Warning] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001168 seconds.
You can set `force_row_wise=true` to remove

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[20]	training's rmse: 34997.3	valid_1's rmse: 35407
[30]	training's rmse: 26653.4	valid_1's rmse: 28377.2
[40]	training's rmse: 22165.9	valid_1's rmse: 24632.3
[50]	training's rmse: 19510.3	valid_1's rmse: 22750.8
[60]	training's rmse: 17912.7	valid_1's rmse: 21752.3
[70]	training's rmse: 16701.8	valid_1's rmse: 21115.5
[80]	training's rmse: 15789.8	valid_1's rmse: 20662.1
[90]	training's rmse: 15255.5	valid_1's rmse: 20478.8
[100]	training's rmse: 14694.2	valid_1's rmse: 20192.9
[110]	training's rmse: 14284.7	valid_1's rmse: 20023.5
[120]	training's rmse: 13923.1	valid_1's rmse: 19887.2
[130]	training's rmse: 13583.9	valid_1's rmse: 19737.9
[140]	training's rmse: 13270.9	valid_1's rmse: 19599.3
[150]	training's rmse: 12980.1	valid_1's rmse: 19419.6
[160]	training's rmse: 12732.5	valid_1's rmse: 19366.9
[170]	training's rmse: 12506.8	valid_1's rmse: 19278.1
[180]	training's rmse: 12280.7	valid_1's rmse: 19179.2
[190]	training's rmse: 12050.6	valid_1's rmse: 19160.3
[200]	training's rms

/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:181: UserWarning: 'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. Pass 'early_stopping()' callback via 'callbacks' argument instead.
  _log_warning("'early_stopping_rounds' argument is deprecated and will be removed in a future release of LightGBM. "
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/basic.py:2068: UserWarning: categorical_feature in Dataset is overridden.
New categorical_feature is ['100m^2以上', '50m^2以上75m^2未満', '75m^2以上100m^2未満', 'D', 'K', 'L', 'S', 'バス・トイレ別', '定期借家', '建物構造', '所在地', '最寄り駅']
  _log_warning('categorical_feature in Dataset is overridden.\n'
/Users/koshidatatsuo/python/signate/mynabi/venv/lib/python3.10/site-packages/lightgbm/engine.py:239: UserWarning: 'verbose_eval' argument is deprecated and will be removed in a future release of LightGBM. Pass 'log_evaluation()' callback

[10]	training's rmse: 48738.9	valid_1's rmse: 51072
[20]	training's rmse: 34966	valid_1's rmse: 36939.4
[30]	training's rmse: 27138.6	valid_1's rmse: 28851.6
[40]	training's rmse: 22803.8	valid_1's rmse: 24314
[50]	training's rmse: 20210.6	valid_1's rmse: 21719
[60]	training's rmse: 18574	valid_1's rmse: 20167.7
[70]	training's rmse: 17449.2	valid_1's rmse: 19189.6
[80]	training's rmse: 16666.8	valid_1's rmse: 18552.8
[90]	training's rmse: 15968.4	valid_1's rmse: 18134.7
[100]	training's rmse: 15456	valid_1's rmse: 17853
[110]	training's rmse: 15004.3	valid_1's rmse: 17576.6
[120]	training's rmse: 14594.6	valid_1's rmse: 17405.8
[130]	training's rmse: 14191.6	valid_1's rmse: 17154.4
[140]	training's rmse: 13854.4	valid_1's rmse: 16944.2
[150]	training's rmse: 13526.1	valid_1's rmse: 16752.4
[160]	training's rmse: 13238.4	valid_1's rmse: 16620.7
[170]	training's rmse: 12958	valid_1's rmse: 16500.2
[180]	training's rmse: 12660.1	valid_1's rmse: 16346.1
[190]	training's rmse: 12428.9	vali

GOSSにおいては、「温水洗浄便座」と「方角」を除いた全てを入力した方が良さそうである

In [11]:
df = pd.read_csv('../data/outer_data/test.csv')
id = df['id']
y_pred = pd.DataFrame(y_pred)
result = pd.concat([id, y_pred],axis=1)
result.to_csv('../data/result_data/GOSS_cv_result.csv',index=False)